In [2]:
import time
import os
import shutil
import csv
import torch
import numpy as np
import math
import itertools
from itertools import product
import torch.nn.functional as F
import pandas as pd
from scipy.stats import poisson
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print("CUDA AVAILABLE" if device=='cuda' else "cuda NOT available")

cuda NOT available


In [3]:
def soft_shift_poisson(rate:int, left_shift:int=0) -> float:
    """
    Returns the mathematical expectation of max(0,X-left_shift), where X a Poisson distribution.
    """
    if left_shift == 0: return rate
    sub_probability = poisson.cdf(2*left_shift-1,rate)
    sub_mean =  0
    for n in range(2*left_shift): sub_mean += n*poisson.pmf(n,rate)
    remaining_mean = rate - sub_mean
    remaining_probability = 1 - sub_probability
    return remaining_mean - remaining_probability*left_shift

In [66]:
class ground_model:
    """
    Definition and operations for a radio resource allocation problem.
    Parameters:
    max_size = maximum number of bits in an user equipment's queue;
    number of user equipments; number of resource blocks;
    default_arrival_rates: indicate if the arrival rate at each user equipment's buffer is set to default
    CQIs_are_equal: indicates if the chanel quality index is constant in the UE and in the RB;
    CQI_base = number of bits scheduled for transmission when CQI=1;
    coef_of_drop, coef_of_latency, power_of_drop, power_of_latency = α, β, x, y:
    cost = α*(cost for rejection)**x + β(cost for latency)**y;
    discount factor;
    precision = bound of the difference between the calculated and the optimal value function of the MDP;
    path = location of the results of the operations (if it is not indicated from the root, the location is in the current directory).
    """
    
    def __init__(self, max_size:int=3, number_UEs:int=6, number_RBs:int=2, 
                 default_arrival_rates=None,
                 CQIs_are_equal=True, CQI_base:float=1,
                 coef_of_drop:float=1, coef_of_latency:float=1, power_of_drop:float=1, power_of_latency:float=1, 
                 discount_factor:float=0.9, precision:float=1e-6,
                 path=None) -> None:
        
        # States and actions
        number_states, number_actions = (max_size + 1) ** number_UEs, number_UEs ** number_RBs
        range_UE_indices = torch.tensor(range(number_UEs))
        range_number_bits = torch.tensor(range(max_size+1))
        list_states = list(product(range_number_bits,repeat=number_UEs))
        list_actions = list(product(range_UE_indices, repeat=number_RBs))
        
        # Send to the device: the data, the ranges for indices, the states and the actions
        self.max_size = torch.tensor([max_size],dtype=int).to(device)
        self.number_UEs, self.number_RBs = torch.tensor([number_UEs],dtype=int).to(device), torch.tensor([number_RBs],dtype=int).to(device)
        self.coef_of_drop, self.coef_of_latency = torch.tensor([coef_of_drop],dtype=float).to(device), torch.tensor([coef_of_latency],dtype=float).to(device)
        self.power_of_drop, self.power_of_latency = torch.tensor([power_of_drop],dtype=float).to(device), torch.tensor([power_of_latency],dtype=float).to(device)
        self.discount_factor, self.precision = torch.tensor([discount_factor], dtype=float).to(device), torch.tensor([precision], dtype=float).to(device)
        self.number_states, self.number_actions = torch.tensor([number_states]).to(device), torch.tensor([number_actions]).to(device)
        self.range_UE_indices, self.range_RB_indices = torch.tensor(range(number_UEs)).to(device), torch.tensor(range(number_RBs)).to(device)
        self.range_state_indices, self.range_action_indices = torch.tensor(range(number_states)).to(device), torch.tensor(range(number_actions)).to(device)
        self.states_matrix, self.actions_matrix = torch.tensor(list_states).to(device), torch.tensor(list_actions).to(device)
        self.empty_buffer = torch.zeros([self.number_UEs],dtype=int).to(device)                      # Number of bits in each UE's empty buffer
        self.full_buffer = self.max_size*torch.ones([self.number_UEs],dtype=int).to(device)          # Number of bits in each UE's full buffer
        
        # Get the arrival rates
        if default_arrival_rates==None:
            vector_arrival_rates = torch.ones([self.number_UEs]).to(device)
            fraction = torch.tensor([max_size/3],dtype=float).to(device)
            print(f"Arrival rate is set to default for each UE: lambda = {fraction.item()}")
            vector_arrival_rates = fraction*vector_arrival_rates
        else:
            vector_arrival_rates = torch.ones([self.number_UEs]).to(device)
            print("Setting the arrival rate for each UE.")
            decision = input("Same arrival rate? (y/n)")
            if "Y" in decision.upper():
                value_ = float(input("For all UE, arrival rate is: "))
                value_ = torch.tensor([value_],dtype=float).to(device)
                vector_arrival_rates = value_*vector_arrival_rates
            else:
                for i in self.range_UE_indices:
                    print(f"Arrival rate for UE {i}: ")
                    vector_arrival_rates[i] = float(input())
        self.vector_arrival_rates = vector_arrival_rates
        
        # Get the chanel quality indices (CQIs) matrix
        if CQIs_are_equal:
            self.CQI_matrix = CQI_base*torch.ones([self.number_UEs,number_RBs],dtype=float).to(device)
        else:
            self.CQI_matrix = torch.ones([self.number_UEs,number_RBs],dtype=float)
            print("Definition of the chanel quality indices.")
            decision = input("Allow various values of CQI? (y/n): ")
            if "Y" in decision.upper():
                print("\nFor each UE and each RB, let's define the CQI as:  CQI = (coef of UE and RB)*(common base)")
                print("Enter all the coefficients. Later on, you will enter the common base to multiply.")
                for i,j in product(self.range_UE_indices,self.range_RB_indices):
                    print(f"    Coefficient for UE {i} and RB {j}: ", end="")
                    time.sleep(0.4)
                    value_ = input()
                    if value_.isnumeric(): 
                        print(value_)
                        value_ = torch.tensor([float(value_)],dtype=float).to(device)
                        self.CQI_matrix[i,j] = value_
                value_ = input("Enter the common base: ")
                if value_.isnumeric(): 
                    value_ = torch.tensor([float(value_)],dtype=float).to(device)
                    CQI_base = value_
                self.CQI_matrix = CQI_base*self.CQI_matrix
                self.CQI_matrix = self.CQI_matrix.to(device)
                
        # Prepare the resolution
        self.prepare_resolution()
        
    def prepare_resolution(self, directory_root=None, solution=None, from_scratch = True):
        
        # Prepare the path for the solution and the simulations
        if from_scratch:
            if directory_root == None:
                this_directory = os.getcwd()
                solution_directory = "Solution_for_B-" + str(self.max_size.item()) + "_UE-" + str(self.number_UEs.item()) + "_RB-" + str(self.number_RBs.item())
                directory_root = os.path.join(this_directory, solution_directory)
            last_index = 1
            while True:
                directory = (directory_root if last_index==1 else directory_root + "_"+str(last_index))
                if os.path.exists(directory):
                    print(f"Directory {directory} serves for the resolution.")
                    decision = input("Continue the last resolution in it? (Y/N): ")
                    if "Y" in decision.upper(): break
                    else:
                        print(f"This is, you should decide wether delete the existing resolution in {directory}")
                        print("and start a new resolution in this directory or let me look for another directory.")
                        decision = input("Start a new resolution in it? (Y/N): ")
                        if "Y" in decision.upper():
                            shutil.rmtree(directory)
                            os.makedirs(directory)
                            break
                        else: last_index += 1
                else:
                    os.makedirs(directory)
                    break
            self.directory = directory
        
        # Prepare the initial value for the backup iteration and save it in a dedicated file
        solution_path = os.path.join(self.directory, "ground_solution.pth")
        if os.path.exists(solution_path):
            if solution == None: self.solution = torch.load(solution_path).to(device)
            else:
                self.solution = solution
                torch.save(self.solution, solution_path)
        else:
            self.solution = (torch.zeros([2,self.number_states],dtype=float).to(device) if solution==None else solution)
            torch.save(self.solution, solution_path)
        self.solution_path = solution_path
        
        # Prepare the file to store the error of running the backup iteration
        self.error_path = error_path = os.path.join(self.directory, "ground_error.txt")
        if os.path.exists(error_path):
            with open(error_path, "r") as f:
                error = f.read()
                self.error = (float(error) if error.isnumeric() else "#NA")
        else:
            with open(error_path, "w") as f:
                self.error = "#NA"
                f.write(self.error)
        
    
    def remainder_fn(self, state:torch.tensor, action:torch.tensor) -> torch.tensor:
        """
        Returns the number of bits remaining in each UE's buffer if action of index action_index was taken in state of index state_index.
        """
        schedule = torch.zeros([self.number_UEs],dtype=float).to(device)  # Number of bits scheduled for transmission
        for i,j in product(self.range_UE_indices,self.range_RB_indices): 
            if action[j]==i:
                schedule[i] += self.CQI_matrix[i,j]
        schedule = schedule.to(int)
        angry_remainder = state - schedule    # Number of remaining bits if negative values are possible
        return torch.max(self.empty_buffer, angry_remainder)
    
    def transition_probability_fn(self, state1:torch.tensor, action:torch.tensor, state2:torch.tensor) -> torch.tensor:
        def UE_transition_probability_fn(rest:int, rate:float, next:int) -> torch.tensor:
            max_size = self.max_size
            sure, impossible = torch.tensor([1],dtype=float).to(device), torch.tensor([0],dtype=float).to(device)
            if next<rest:     return impossible                                                           # next < rest
            if next<max_size: return torch.tensor([poisson.pmf(next-rest,rate)],dtype=float).to(device)   # rest ≤ next < max_size  
            range_next = torch.tensor(range((max_size-rest).item()),dtype=int).to(device)                 # next = max_size, then  P{size=next} = 1 - P{arrival<}
            probability = sure
            for arrival in range_next:
                probability_arrival = torch.tensor([poisson.pmf(arrival,rate)],dtype=float).to(device)
                probability = probability - probability_arrival
            return probability
        rate = self.vector_arrival_rates
        remainder = self.remainder_fn(state1,action)
        probability = torch.tensor([1],dtype=float).to(device)
        for i in self.range_UE_indices:                                                                    # i = queue index
            probability = probability * UE_transition_probability_fn(remainder[i], rate[i], state2[i])
        return probability
    
    def cost_fn(self, state:torch.tensor, action:torch.tensor) -> torch.tensor:
        def exact_cost_fn(remainder:torch.tensor, state2:torch.tensor) -> torch.tensor:                     # Exact cost associated with the transition from state1 to state2
            def partial_cost_fn(rest:torch.tensor, arrival:torch.tensor) -> torch.tensor:                   # Cost for transition of the queue
                false_excess = arrival + rest - self.max_size
                excess = torch.max(nothing, false_excess)
                return self.coef_of_drop * excess**self.power_of_drop + self.coef_of_latency * rest**self.power_of_latency
            
            exact_cost = torch.tensor([0],dtype=float).to(device)
            for q in self.range_UE_indices:
                if state2[q] < remainder[q]:                                                                 # The transition is impossible
                    exact_cost = torch.tensor([0],dtype=float).to(device)
                    break
                else:
                    arrival = state2[q] - remainder[q]
                    exact_cost = exact_cost + partial_cost_fn(remainder[q], arrival)
            return exact_cost
        
        nothing = torch.tensor([0],dtype=int).to(device)
        remainder = self.remainder_fn(state, action)
        cost = torch.tensor([0],dtype=float).to(device)
        for s in self.range_state_indices:
            possible_state = self.states_matrix[s]
            possible_exact_cost = exact_cost_fn(remainder, possible_state)
            cost = cost + possible_exact_cost * self.transition_probability_fn(state,action,possible_state)
        return cost
    
    def resolution(self, directory=None, solution=None, precision=None) -> torch.tensor:
        
        # Initialization
        if directory == None: 
            directory = self.directory
            from_scratch = False
        else:
            from_scratch = True
        if precision == None: precision = self.precision
        self.prepare_resolution(directory, solution, from_scratch)
        
        # Body of the resolution
        gamma = self.discount_factor.item()
        gamma_prime = gamma / (1-gamma)
        old_value = self.solution[1].to(device)
        new_value = self.solution[1].to(device)
        current_policy, current_value = self.solution[0].to(device), self.solution[1].to(device)
        policy = torch.zeros([self.number_states],dtype=int).to(device)
        error = self.error
        step = 0
        try:
            while True:
                for s in self.range_state_indices:
                    step += 1
                    print(f"Ground model resolution.   Updating the value (step {step}).  Current error: {error};  current state: s_{s}", end="\r")
                    state1 = self.states_matrix[s]
                    Q = torch.zeros([self.number_actions],dtype=float).to(device)
                    for a in self.range_action_indices:
                        action = self.actions_matrix[a]
                        P = torch.zeros([self.number_states],dtype=float).to(device)
                        for s2 in self.range_state_indices: 
                            state2 = self.states_matrix[s2]
                            P[s2] = self.transition_probability_fn(state1, action, state2)
                        Q[a] = self.cost_fn(state1,action) + self.discount_factor*torch.sum(old_value*P)
                    new_value[s] = torch.min(Q)
                    policy[s] = torch.argmin(Q)
                current_policy, current_value = policy, new_value
                diff = torch.abs(new_value - old_value)
                max_diff = torch.max(diff).item() 
                error = gamma_prime * max_diff
                if error <= precision: break
        except KeyboardInterrupt:
            pass 
        print(f"Ground model resolution.   Updating the value (step {step}).  Current error: {error};  current state: s_{s}", end="\r")
        
        # Storing the solution and the error
        self.solution = torch.stack([current_policy, current_value])
        torch.save(self.solution, self.solution_path)
        with open(self.error_path, "w") as f:
            f.write(str(error))

In [71]:
class abstract_model:
    """Make and solve an abstract model corresponding to a ground model

    Args:
        model (ground_model): the ground model on which the abstract model is built.
        number_groups (int, optional): number of groups of UEs fo the abstract model. Defaults to 3.
        coef_owners (str, optional): the object that recieve a weight: "UEs" or "groups". Defaults to "UEs".
        coef_distribution_criterion (str, optional): criterion to weight these objects: 
        "uniform" weighting, by "simularity" or by "dissimilarity". Defaults to "uniform".
        variant (str, optional): variant for the coefficient distribution criterion: "standard deviation" (or "sd"),
        "cross entropy" (or "cross") or "total difference" (or "Gini index" or "Gini"). Necessary for groups dissimilarity. Defaults to "sd".        
        selection_mode (str, optional): number of representatives in each class: "one", the top weighted ("top") or "all". Defaults to "one".
    """
    
    def __init__(self, model:ground_model, number_groups:int=3, coef_owners="UEs", coef_distribution_criterion="uniform", variant=None, selection_mode="one"): 
        
        # Get ready to use the entered parameters
        if coef_owners == None or coef_owners.upper() in ["UES", "UE"] : coef_owners = "UEs"
        elif coef_owners.upper() in ["GROUP", "GROUPS"]: coef_owners = "groups"
        else:
            print(f'The definition of the abstract model is broken. Cause: objects to weights "{coef_owners}"' + 
                  'has unexpected value. Correct values: "UEs" and "groups".')
            return
        
        if coef_distribution_criterion == None or "UNIF" in coef_distribution_criterion.upper(): 
            coef_distribution_criterion = "uniform"
        elif "DIS" in coef_distribution_criterion.upper(): coef_distribution_criterion = "dissimilarity"
        elif "SIM" in coef_distribution_criterion.upper(): coef_distribution_criterion = "similarity"
        else:
            print(f'The definition of the abstract model is broken. Cause: weighting criterion "{coef_distribution_criterion}' + 
                  'has unexpected value. Correct values: "uniform", "similarity" and "dissimilarity".')
            return
        
        if selection_mode == None or selection_mode == 1 or selection_mode.upper() in ["1", "ONE"]: selection_mode = "one"
        elif "TOP" in selection_mode.upper() or "MOST" in selection_mode.upper(): selection_mode = "top"
        elif selection_mode.upper() in ["ALL", "AL"]: selection_mode = "all"
        else:
            print(f'The definition of the abstract model is broken. Cause: selection mode "{selection_mode}' + 
                  'has unexpected value. Correct values: "one", "top" and "all".')
            return
        
        if coef_owners == "groups" and coef_distribution_criterion == "dissimilarity":
            if variant == None or "ST" in variant.upper() or "SD" in variant.upper(): variant = "sd"
            elif "CROS" in variant.upper(): variant = "cross"
            elif "GINI" in variant.upper() or "TOTAL" in variant.upper(): variant = "gini"
            else:
                print(f'The definition of the abstract model is broken. Cause: variant "{coef_distribution_criterion}' + 
                    'has unexpected value. Correct values for group dissimilarity: "standard deviation", "cross entropy" and "Gini index".')
                return
        else: variant = None
        
        self.model = model
        self.number_groups = torch.tensor(number_groups,dtype=int).to(device)
        self.coef_owners, self.coef_distribution_criterion, self.selection_mode = coef_owners, coef_distribution_criterion, selection_mode
        self.variant = variant
        
        self.make_groups_UEs()  # Group the UEs in groups. Result: group_indices_vector and groups_list, number of UEs per group
        self.make_abstraction()  # Make the abstract states, the abstraction function and the list of classes
        self.make_weights_distribution()  # Built the vector representing the weight distribution
        
        
    def make_groups_UEs(self) -> torch.tensor:  # Group the UEs in groups
        def grouping(N):
            model = self.model
            characteristics_vector = model.number_UEs/model.number_RBs*torch.sum(model.CQI_matrix,dim=1) - model.vector_arrival_rates
            if N >= model.number_UEs:
                if characteristics_vector.unique().size(0) == characteristics_vector.size(0):
                    sorted_indices = torch.argsort(characteristics_vector)
                    num_elements = characteristics_vector.size(0)
                    vector_groups = torch.zeros(num_elements, dtype=torch.long)
                    vector_groups[sorted_indices] = torch.arange(num_elements)
                    return vector_groups
                else:
                    return grouping(model.number_UEs.item() - 1)
            quantiles = torch.linspace(0, 1, N+1)[1:-1].to(float).to(device)
            bounds_characteristics = torch.quantile(characteristics_vector, quantiles)
            _, group_indices_vector = torch.searchsorted(bounds_characteristics, characteristics_vector.unsqueeze(1), right=True).squeeze(1).unique(return_inverse=True)
            return group_indices_vector
        
        self.group_indices_vector = grouping(self.number_groups)
        self.number_groups = self.group_indices_vector.unique().size(0)
        self.range_group_indices = torch.tensor(range(self.number_groups),dtype=int)
        self.groups_list = [torch.where(self.group_indices_vector==g)[0] for g in self.range_group_indices]
        groups_size_list = [self.groups_list[g].size(0) for g in self.range_group_indices]
        self.groups_size_vector = torch.tensor(groups_size_list,dtype=int).to(device)
    
    def make_abstraction(self):  # Make the abstract states, the abstraction function and the list of classes
        model = self.model
        
        # Build the abstract states
        max_size_groups = torch.zeros([self.number_groups],dtype=int).to(device)
        for g in self.range_group_indices: max_size_groups[g] = model.max_size * self.groups_list[g].size(0)
        states = itertools.product(*[range(size+1) for size in max_size_groups])
        self.states_matrix = torch.tensor(list(states))
        self.number_states = self.states_matrix.size(0)
        
        # Build the abstract function as a vector called abstraction_vector. abstraction_vector[gs_idx] is the index 
        # of the abstracte corresponding to ground state of index gs_idx
        self.abstraction_vector = torch.zeros([model.number_states],dtype=int)
        for gs_idx in model.range_state_indices:
            print(f"Getting the abstraction function.  Ground state {gs_idx+1} " + 
                  f"/ {model.number_states.item()+1}  ({(gs_idx+1)/(model.number_states+1).item():.0%})", end="\r")
            ground_state = model.states_matrix[gs_idx]
            abstract_state = torch.zeros([self.number_groups],dtype=int)
            for g in self.range_group_indices:
                abstract_state[g] = ground_state[self.groups_list[g]].sum()
            for as_idx, row in enumerate(self.states_matrix):
                if torch.all(row == abstract_state):
                    self.abstraction_vector[gs_idx] = as_idx
                    break
        print("\r",end="\r")
        
        # Build the list of classes. calasses_list[c_idx] is the class (vector of ground state indices) of ground states 
        # whom abstract state is of index s_idx
        self.range_class_indices = torch.tensor(range(self.number_states),dtype=int)
        self.classes_list = [torch.where(self.abstraction_vector==c_idx)[0] for c_idx in self.range_class_indices]
    
    
    def make_weights_distribution(self):  # Built the vector representing the weight distribution
        def selection_fn(weight_distribution:torch.tensor, selection_mode:str) -> torch.tensor:  # Return a final weight distribution 
            # corresponding to the selection mode
            pass
        
        def weight_fn(distribution:torch.tensor) -> torch.tensor:  # Return a weight distribution any distribution of positive numbers on the states
            pass
        
        def preweight_fn() -> torch.tensor:  # Distribute numbers on states according to the weights of UEs or groups
            pass
        
        def coef_fn(state_idx:int) -> torch.tensor:  # Make a coefficient distribution on UEs or groups
            state = self.states_matrix[state_idx]
            # according to a state
            criterion, coef_owners, variant = self.coef_distribution_criterion, self.coef_owners, self.variant
            if criterion == "uniform":
                return (torch.ones([self.model.number_UEs],dtype=float).to(device) 
                        if coef_owners=="UEs" 
                        else torch.ones([self.number_groups],dtype=float).to(device))
            abstract_state_idx = self.abstraction_vector[state_idx]
            abstract_state = self.states_matrix[abstract_state_idx]
            if coef_owners == "UEs":  # criterion ≠ "uniform" and coef_owners = "UEs"
                group_means_vector = abstract_state / self.groups_size_vector
                deviations_vector = torch.zeros([self.model.number_UEs],dtype=float).to(device)
                for ue in self.model.range_UE_indices:
                    g_idx = self.group_indices_vector[ue]
                    deviations_vector[ue] = torch.abs(state[ue] - group_means_vector[g_idx])
                return (torch.exp(-deviations_vector) if criterion=="similarity" else deviations_vector)  # else means "dissimilarity"
            # criterion ≠ "uniform" and coef_owners = "groups"
            coefs_vector = torch.zeros([self.number_groups],dtype=float).to(device)
            if criterion == "similarity":  # criterion = "similarity" and coef_owners = "groups"
                for g_idx in self.range_group_indices:
                    states_idxs = torch.where(self.group_indices_vector==g_idx)[0]
                    state_restriction = self.states_matrix[states_idxs]
                    num_UEs = self.groups_size_vector[g_idx]
                    num_bits = abstract_state[g_idx]
                    redistribution = torch.full((num_UEs),num_bits)
                    coefs_vector[g_idx] = F.cosine_similarity(state_restriction,redistribution,dim=0)
                return coefs_vector
            # criterion == "dissimilarity" and coef_owners = "groups"
            if variant == "sd":  # criterion == "dissimilarity", coef_owners = "groups" and variant = "sd"
                for g_idx in self.range_group_indices:
                    num_bits = abstract_state[g_idx]
                    average_num_bits = num_bits / self.groups_size_vector[g_idx]
                    redistribution = torch.full((num_UEs),average_num_bits)
                    states_idxs = torch.where(self.group_indices_vector==g_idx)[0]
                    state_restriction = self.states_matrix[states_idxs]
                    square_deviations_vector = (state_restriction - redistribution)**2
                    variance = math.sqrt(torch.sum(square_deviations_vector))
                    coefs_vector[g_idx] = variance / num_bits
                return coefs_vector
            if variant == "cross":  # criterion == "dissimilarity", coef_owners = "groups" and variant = "cross"
                # Normalize the state in each group
                normalized_state = torch.zeros([self.states],dtype=float).to(device)
                for ue in self.self.range_UE_indices:
                    g_idx = self.group_indices_vector[ue]
                    normalized_state[ue] = state[ue] / abstract_state[g_idx]
                # Get the cross entropy in each group
                for g_idx in self.range_group_indices:
                    states_idxs = torch.where(self.group_indices_vector==g_idx)[0]
                    logarithm = torch.tensor([self.groups_size_vector[g_idx]],dtype=float)
                    coefs_vector[g_idx] = normalized_state[states_idxs].sum()*logarithm
                return coefs_vector
            # criterion == "dissimilarity", coef_owners = "groups" and variant = "gini"
            two = torch.tensor([2],dtype=float).to(device)
            for g_idx in self.range_group_indices:
                if abstract_state[g_idx] != 0:
                    states_idxs = torch.where(self.group_indices_vector==g_idx)[0]
                    sum_dif = torch.tensor([0],dtype=float).to(device)
                    for i in states_idxs:
                        for j in states_idxs:
                            sum_dif = sum_dif + torch.abs(state[i] - state[j])
                    coefs_vector[g_idx] = sum_dif / two / self.groups_list[g_idx] / abstract_state[g_idx]
            return coefs_vector
        self.coef = coef_fn(49)
        return None
        model = self.model
        number_groups = self.number_groups
        coef_owners, coef_distribution_criterion, selection_mode = self.coef_owners, self.coef_distribution_criterion, self.selection_mode

In [67]:
m = ground_model(CQIs_are_equal=False)

Arrival rate is set to default for each UE: lambda = 1.0
Definition of the chanel quality indices.



For each UE and each RB, let's define the CQI as:  CQI = (coef of UE and RB)*(common base)
Enter all the coefficients. Later on, you will enter the common base to multiply.
    Coefficient for UE 0 and RB 0: 3
    Coefficient for UE 0 and RB 1: 2
    Coefficient for UE 1 and RB 0: 2
    Coefficient for UE 1 and RB 1: 3
    Coefficient for UE 2 and RB 0: 3
    Coefficient for UE 2 and RB 1: 3
    Coefficient for UE 3 and RB 0: 3
    Coefficient for UE 3 and RB 1: 1
    Coefficient for UE 4 and RB 0: 1
    Coefficient for UE 4 and RB 1: 1
    Coefficient for UE 5 and RB 0: 4
    Coefficient for UE 5 and RB 1: 4


In [77]:
am = abstract_model(m,3,"ues", "simi", "oNe")
# am.number_states

Getting the abstraction function.  Ground state 4096 / 4097  (100%)

IndexError: index 3 is out of bounds for dimension 0 with size 3

In [76]:
print(am.coef)

tensor([1., 1., 1.], dtype=torch.float64)


In [63]:
A = torch.tensor([1,4],dtype=float)
B = torch.tensor([0,1],dtype=float)
print(math.sqrt(A.sum()))

2.23606797749979


In [10]:
# TEST FOR TRANSITION PROBABILITIES

max_diff = 0
for ai in range(m.number_actions):
    AT = m.actions_matrix[ai]
    AN = AT.numpy()
    print(f"\n\nWith action a_{ai} = {AN}\n")
    for si1 in range(m.number_states):
        S1T = m.states_matrix[si1]
        S1N = S1T.numpy()
        S = torch.tensor([0]).to(device)
        for si2 in range(m.number_states):
            S2T = m.states_matrix[si2]
            PT = m.transition_probability_fn(S1T,AT,S2T)
            S = S + PT
            S2N, PN = S2T.numpy(), PT.item()
            print(f"a_{ai}:      {S1N} --->  {S2N}:    P = {PN}")
        SN = S.item()
        print(f"\n                  Sum of probabilities = {SN}\n\n")
        max_diff = max((max_diff, abs(SN-1)))
print(f"\nMax error = {max_diff}")



With action a_0 = [0 0]

a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 0 0]:    P = 0.0009118819655545173
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 0 1]:    P = 0.0009118819655545173
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 0 2]:    P = 0.0004559409827772586
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 0 3]:    P = 0.0001990472627800679
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 1 0]:    P = 0.0009118819655545173
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 1 1]:    P = 0.0009118819655545173
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 1 2]:    P = 0.0004559409827772586
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 1 3]:    P = 0.0001990472627800679
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 2 0]:    P = 0.0004559409827772586
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 2 1]:    P = 0.0004559409827772586
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 2 2]:    P = 0.00022797049138862928
a_0:      [0 0 0 0 0 0 0] --->  [0 0 0 0 0 2 3]:    P = 9.952363139003394e-05
a_0:      [0 0 0 0 0 0 0] --->  [0 0

KeyboardInterrupt: 

In [11]:
m.resolution()

In [33]:
for s in m.range_state_indices:
    action_number = m.solution[0,s].to(int).item()
    state = m.states_matrix[s].numpy()
    action = m.actions_matrix[action_number].numpy()
    print(f"State {state}  --->   {action}")

State [0 0 0]  --->   [0 0 0]
State [0 0 1]  --->   [0 0 2]
State [0 0 2]  --->   [0 2 2]
State [0 0 3]  --->   [2 2 2]
State [0 1 0]  --->   [0 0 1]
State [0 1 1]  --->   [0 1 2]
State [0 1 2]  --->   [1 2 2]
State [0 1 3]  --->   [2 2 2]
State [0 2 0]  --->   [0 1 1]
State [0 2 1]  --->   [1 1 2]
State [0 2 2]  --->   [1 2 2]
State [0 2 3]  --->   [2 2 2]
State [0 3 0]  --->   [1 1 1]
State [0 3 1]  --->   [1 1 2]
State [0 3 2]  --->   [1 2 2]
State [0 3 3]  --->   [1 1 1]
State [1 0 0]  --->   [0 0 0]
State [1 0 1]  --->   [0 0 2]
State [1 0 2]  --->   [0 2 2]
State [1 0 3]  --->   [2 2 2]
State [1 1 0]  --->   [0 0 1]
State [1 1 1]  --->   [0 1 2]
State [1 1 2]  --->   [1 2 2]
State [1 1 3]  --->   [2 2 2]
State [1 2 0]  --->   [0 1 1]
State [1 2 1]  --->   [1 1 2]
State [1 2 2]  --->   [1 2 2]
State [1 2 3]  --->   [2 2 2]
State [1 3 0]  --->   [1 1 1]
State [1 3 1]  --->   [1 1 2]
State [1 3 2]  --->   [1 2 2]
State [1 3 3]  --->   [1 1 1]
State [2 0 0]  --->   [0 0 0]
State [2 0

In [7]:
m.solution

tensor([[ 0.0000,  2.0000,  8.0000, 26.0000,  1.0000,  5.0000, 17.0000, 26.0000,
          4.0000, 14.0000, 17.0000, 26.0000, 13.0000, 14.0000, 13.0000, 13.0000,
         13.0000, 14.0000, 17.0000, 26.0000, 13.0000, 14.0000, 17.0000, 26.0000,
         26.0000, 14.0000, 26.0000, 26.0000, 13.0000, 14.0000, 13.0000, 13.0000,
         13.0000, 14.0000, 17.0000, 26.0000, 26.0000, 26.0000, 26.0000, 26.0000,
         26.0000, 26.0000, 26.0000, 26.0000, 26.0000, 14.0000, 14.0000, 13.0000,
         13.0000, 13.0000, 13.0000, 13.0000, 26.0000, 26.0000, 26.0000, 26.0000,
         26.0000, 26.0000, 26.0000, 26.0000, 26.0000, 26.0000,  5.0000,  1.0000],
        [11.9300, 12.4646, 13.0231, 13.3148, 13.4451, 14.0475, 14.6770, 15.4104,
         15.1565, 15.4961, 16.9346, 17.3383, 16.1178, 18.0024, 20.0852, 21.5080,
         13.8497, 14.4703, 15.1187, 15.4574, 15.6086, 16.3080, 17.0387, 17.5813,
         17.5051, 17.9846, 19.0954, 19.5232, 18.6969, 20.5640, 22.6692, 24.0862,
         15.5854, 16.2838, 

In [8]:
# TEST OF COSTS

list_rests = list_costs = []
for a,s in product(m.range_action_indices,m.range_state_indices):
    action, state = m.actions_matrix[a], m.states_matrix[s]
    remainder = m.remainder_fn(state,action)
    cost = m.cost_fn(state, action)
    list_rests.append(torch.sum(remainder).item())
    list_costs.append(cost.item())
    print(f"Action {action.numpy()}  in state {state.numpy()}      --->      Rest = {remainder.numpy()}  and Cost = {cost.item()}")
print(f"\nThe correlation coefficient between the cost and the sum of the rest in UE buffers is {np.corrcoef(list_costs,list_rests)[0,1]}")

Action [0 0 0]  in state [0 0 0]      --->      Rest = [0 0 0]  and Cost = 11.9299892206712
Action [0 0 0]  in state [0 0 1]      --->      Rest = [0 0 1]  and Cost = 13.849687823599814
Action [0 0 0]  in state [0 0 2]      --->      Rest = [0 0 2]  and Cost = 15.58544670594269
Action [0 0 0]  in state [0 0 3]      --->      Rest = [0 0 3]  and Cost = 16.953326147114137
Action [0 0 0]  in state [0 1 0]      --->      Rest = [0 1 0]  and Cost = 13.849687823599814
Action [0 0 0]  in state [0 1 1]      --->      Rest = [0 1 1]  and Cost = 15.769386426528415
Action [0 0 0]  in state [0 1 2]      --->      Rest = [0 1 2]  and Cost = 17.505145308871302
Action [0 0 0]  in state [0 1 3]      --->      Rest = [0 1 3]  and Cost = 18.873024750042745
Action [0 0 0]  in state [0 2 0]      --->      Rest = [0 2 0]  and Cost = 15.585446705942692
Action [0 0 0]  in state [0 2 1]      --->      Rest = [0 2 1]  and Cost = 17.505145308871302
Action [0 0 0]  in state [0 2 2]      --->      Rest = [0 2 2] 

In [28]:
state = torch.tensor([3,0,0])
for a in m.range_action_indices:
    action = m.actions_matrix[a]
    cost = m.cost_fn(state,action).item()
    rest = m.remainder_fn(state,action).numpy()
    print(f"a_{a} = {action.numpy()} in {state.numpy()}: rest = {rest},  cost = {cost}")

a_0 = [0 0 0] in [3 0 0]: rest = [0 0 0],  cost = 11.9299892206712
a_1 = [0 0 1] in [3 0 0]: rest = [1 0 0],  cost = 13.849687823599808
a_2 = [0 0 2] in [3 0 0]: rest = [1 0 0],  cost = 13.849687823599808
a_3 = [0 1 0] in [3 0 0]: rest = [1 0 0],  cost = 13.849687823599808
a_4 = [0 1 1] in [3 0 0]: rest = [2 0 0],  cost = 15.585446705942692
a_5 = [0 1 2] in [3 0 0]: rest = [2 0 0],  cost = 15.585446705942692
a_6 = [0 2 0] in [3 0 0]: rest = [1 0 0],  cost = 13.849687823599808
a_7 = [0 2 1] in [3 0 0]: rest = [2 0 0],  cost = 15.585446705942692
a_8 = [0 2 2] in [3 0 0]: rest = [2 0 0],  cost = 15.585446705942692
a_9 = [1 0 0] in [3 0 0]: rest = [1 0 0],  cost = 13.849687823599808
a_10 = [1 0 1] in [3 0 0]: rest = [2 0 0],  cost = 15.585446705942692
a_11 = [1 0 2] in [3 0 0]: rest = [2 0 0],  cost = 15.585446705942692
a_12 = [1 1 0] in [3 0 0]: rest = [2 0 0],  cost = 15.585446705942692
a_13 = [1 1 1] in [3 0 0]: rest = [3 0 0],  cost = 16.953326147114137
a_14 = [1 1 2] in [3 0 0]: rest 